## Project 2: Data Wrangling and Analysis

> The dataset in on WeRateDogs. WeRateDogs is a Twitter account that rates people's dogs with a humorous comment about the dog. These ratings almost always have a denominator of 10. The numerators, though? Almost always greater than 10. 11/10, 12/10, 13/10, etc. Why? Because "they're good dogs Brent." WeRateDogs has over 4 million followers and has received international media coverage.<br>
> Three different dataset are used <br>
### 1. Enhanced Twitter Archive
> The WeRateDogs Twitter archive contains basic tweet data for all 5000+ of their tweets, but not everything. One column the archive does contain though: each tweet's text, which I used to extract rating, dog name, and dog "stage" (i.e. doggo, floofer, pupper, and puppo) to make this Twitter archive "enhanced."<br>

### 2. Additional Data via the Twitter API
> Used twitter api to scrape on each twet_Id on the Enhanced Twitter Archive to get retweet count and favourite count of each tweet id.
### 3. The tweet image predictions
>A table full of image predictions (the top three only) alongside each tweet ID, image URL, and the image number that corresponded to the most confident prediction (numbered 1 to 4 since tweets can have up to four images).Used request library to download the dataset from udacity using this url[https://d17h27t6h515a5.cloudfront.net/topher/2017/August/599fd2ad_image-predictions/image-predictions.tsv]

In [1]:
import tweepy

import json
import pandas as pd
import numpy as np
from timeit import default_timer as timer


import seaborn as sns
import matplotlib.pyplot as plt

%matplotlib inline
sns.set_style("darkgrid")

In [2]:
# settings to display all columns
pd.set_option("display.max_columns", None)
pd.set_option('display.max_rows', None)  # or 1000

In [3]:
# Variables that contains the credentials to access Twitter API
ACCESS_TOKEN = 'xxxxxxxxxx'
ACCESS_SECRET = 'xxxxxxxxx'
CONSUMER_KEY = 'xxxxxxxxx'
CONSUMER_SECRET = 'xxxxxxxxx'


# Setup access to API
def connect_to_twitter_OAuth():
    auth = tweepy.OAuthHandler(CONSUMER_KEY, CONSUMER_SECRET)
    auth.set_access_token(ACCESS_TOKEN, ACCESS_SECRET)

    api = tweepy.API(auth)
    return api


# Create API object
api = connect_to_twitter_OAuth()

In [4]:
# tweets from my stream
public_tweets = api.home_timeline()
for tweet in public_tweets:
    print(tweet.text)

Crypto hackers are increasingly phishing for new bait on social media https://t.co/5G6O7mnE8y by @jacqmelinek
RT @hackathorn: #DeepLearning depends on the inherent geometry within low-dimensional structures reflecting physical reality. If you agree,…
Tesla reportedly nowhere near goal of installing 1,000 solar roofs a week https://t.co/wkFxABkrUB by @harrisonweber
Brendan Artley outlines an introduction to the mathematics behind neural networks. https://t.co/hsBiCg1lAy
Instacart's new rewards program gives shoppers exclusive early access to orders and more https://t.co/nWMYKmZrYQ by @aiishamalik1
US safety regulators open special investigation into Cruise AV crash https://t.co/ZdBF7Vxw3f by @kirstenkorosec
Amazon bets on influencers to drive sales for Prime Day https://t.co/jV2QmnZbrC by @laurenforristal
Levered up, doubled down https://t.co/jOBs3vpmeA by @anitaramaswamy and @lucasmtny
Former Theranos exec Sunny Balwani is found guilty https://t.co/kauGx9swUx by @asilbwrites
Pitch Deck

### Read on Enhanced Twitter Archive.

In [5]:
archive_df = pd.read_csv('twitter-archive-enhanced.csv')
archive_df.head()

tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
0  892420643555336193                    NaN                  NaN   
1  892177421306343426                    NaN                  NaN   
2  891815181378084864                    NaN                  NaN   
3  891689557279858688                    NaN                  NaN   
4  891327558926688256                    NaN                  NaN   

                   timestamp  \
0  2017-08-01 16:23:56 +0000   
1  2017-08-01 00:17:27 +0000   
2  2017-07-31 00:18:03 +0000   
3  2017-07-30 15:58:51 +0000   
4  2017-07-29 16:00:24 +0000   

                                              source  \
0  <a href="http://twitter.com/download/iphone" r...   
1  <a href="http://twitter.com/download/iphone" r...   
2  <a href="http://twitter.com/download/iphone" r...   
3  <a href="http://twitter.com/download/iphone" r...   
4  <a href="http://twitter.com/download/iphone" r...   

                                                text  retweeted_status_id  \
0  This is Phineas. He's a mystical boy. Only eve...                  NaN   
1  This is Tilly. She's just checking pup on you....                  NaN   
2  This is Archie. He is a rare Norwegian Pouncin...                  NaN   
3  This is Darla. She commenced a snooze mid meal...                  NaN   
4  This is Franklin. He would like you to stop ca...                  NaN   

   retweeted_status_user_id retweeted_status_timestamp  \
0                       NaN                        NaN   
1                       NaN                        NaN   
2                       NaN                        NaN   
3                       NaN                        NaN   
4                       NaN                        NaN   

                                       expanded_urls  rating_numerator  \
0  https://twitter.com/dog_rates/status/892420643...                13   
1  https://twitter.com/dog_rates/status/892177421...                13   
2  https://twitter.com/dog_rates/status/891815181...                12   
3  https://twitter.com/dog_rates/status/891689557...                13   
4  https://twitter.com/dog_rates/status/891327558...                12   

   rating_denominator      name doggo floofer pupper puppo  
0                  10   Phineas  None    None   None  None  
1                  10     Tilly  None    None   None  None  
2                  10    Archie  None    None   None  None  
3                  10     Darla  None    None   None  None  
4                  10  Franklin  None    None   None  None

In [6]:
archive_df.shape

(2356, 17)

In [7]:
# the ID of the status
id = 891815181378084864
  
# fetching the status
status = api.get_status(id)
  
# fetching the retweet_count attribute
retweet_count = status.retweet_count
  
print("The number of time the status has been retweeted is : " + str(retweet_count))

The number of time the status has been retweeted is : 3477


In [8]:
for i in archive_df['tweet_id']:
    #tweet_id = data['tweet_id']
    
    # fetching the status
    status = api.get_status(i)
    
    # fetching the retweet_count attribute
    retweet_count = status.retweet_count
    print(i)
    print(retweet_count)
    
    likes = status.favorite_count
    print(likes)
    
    data_collected ={
        'tweet_id': i,
        'retweet_count': retweet_count,
        'likes': likes
    }
    
    break

892420643555336193
7001
33801


In [9]:
# Query Twitter's API for JSON data for each tweet ID in the Twitter archive
count = 0
fails_dict = {}
start = timer()
missing_tweets = []
# Save each tweet's returned JSON as a new line in a .txt file
with open('tweet_json.txt', 'w') as outfile:
    # This loop will likely take 20-30 min to run 
    for tweet_id in archive_df['tweet_id']:
        count += 1
        print(str(count) + ": " + str(tweet_id))
        try:
            tweet = api.get_status(tweet_id, tweet_mode = 'extended',
                                   wait_on_rate_limit = True,
                                   wait_on_rate_limit_notify = True)
            
            print("Success")
            json.dump(tweet._json, outfile)
            outfile.write('\n')
        except Exception as err_msg:
            print(str(tweet_id)+ " - " + str(err_msg))
            missing_tweets.append(tweet_id)
        
        
end = timer()
print('Entire query twitter data take {} min'.format(
        (end - start)/60))
print(fails_dict)

Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


1: 892420643555336193


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


Success
2: 892177421306343426


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


...

Success
2354: 666033412701032449


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


Success
2355: 666029285002620928


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


Success
2356: 666020888022790149
Success
Entire query twitter data take 89.9547098894 min
{}


In [10]:
len(missing_tweets)

29

In [93]:
missing_tweets_final = [] # A list for the final unretrieved tweetIDs

with open('tweet_json.txt', 'a', encoding='utf8') as file:
    for tweet_id in missing_tweets:
        print(str(count) + ": " + str(tweet_id))
        try:
            tweet = api.get_status(tweet_id, tweet_mode = 'extended',
                                  wait_on_rate_limit = True, 
                                  wait_on_rate_limit_notify = True)
            
            print("Success")
            json.dump(tweet._json, outfile)
            outfile.write('\n')
            
        except Exception as err_msg:
            print(str(tweet_id)+ " - " + str(err_msg))
            missing_tweets_final.append(tweet_id)

Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


2356: 888202515573088257


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


888202515573088257 - 404 Not Found
144 - No status found with that ID.
2356: 873697596434513921


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


...

759923798737051648 - 404 Not Found
144 - No status found with that ID.
2356: 759566828574212096


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


759566828574212096 - 404 Not Found
144 - No status found with that ID.
2356: 754011816964026368


Unexpected parameter: wait_on_rate_limit
Unexpected parameter: wait_on_rate_limit_notify


754011816964026368 - 404 Not Found
144 - No status found with that ID.
2356: 680055455951884288
680055455951884288 - 404 Not Found
144 - No status found with that ID.


In [94]:
len(missing_tweets_final)

29

> Seems 30 tweets from the archive_df are no-longer avaliable

In [95]:
# Collect all selected attributes
selected_attr = []

with open('tweet_json.txt', 'r') as json_file:
    for line in json_file:
        json_data = json.loads(line)
        
        selected_attr.append({
            'tweet_id': json_data['id_str'],
            'retweet_count': json_data['retweet_count'],
            'favorite_count': json_data['favorite_count'],
        })
        

# Save all selected attributes in another dataframe
api_df = pd.DataFrame(selected_attr, columns = [
    'tweet_id', 'retweet_count', 'favorite_count'
])

api_df.head()

tweet_id  retweet_count  favorite_count
0  892420643555336193           7001           33801
1  892177421306343426           5299           29301
2  891815181378084864           3477           22042
3  891689557279858688           7223           36920
4  891327558926688256           7754           35299

In [96]:
api_df.shape

(2327, 3)

### The tweet image predictions
> Used request to download the dataset.

In [14]:
import requests
import csv
res = requests.get('https://d17h27t6h515a5.cloudfront.net/topher/2017/August/599fd2ad_image-predictions/image-predictions.tsv')
with open('image_predictions.tsv', mode='wb') as file:
    file.write(res.content)

In [15]:
image = pd.read_csv('image_predictions.tsv', sep='\t')
image.head()

tweet_id                                          jpg_url  \
0  666020888022790149  https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1  666029285002620928  https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2  666033412701032449  https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3  666044226329800704  https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4  666049248165822465  https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   

   img_num                      p1   p1_conf  p1_dog                  p2  \
0        1  Welsh_springer_spaniel  0.465074    True              collie   
1        1                 redbone  0.506826    True  miniature_pinscher   
2        1         German_shepherd  0.596461    True            malinois   
3        1     Rhodesian_ridgeback  0.408143    True             redbone   
4        1      miniature_pinscher  0.560311    True          Rottweiler   

    p2_conf  p2_dog                   p3   p3_conf  p3_dog  
0  0.156665    True    Shetland_sheepdog  0.061428    True  
1  0.074192    True  Rhodesian_ridgeback  0.072010    True  
2  0.138584    True           bloodhound  0.116197    True  
3  0.360687    True   miniature_pinscher  0.222752    True  
4  0.243682    True             Doberman  0.154629    True

In [16]:
image

tweet_id                                            jpg_url  \
0     666020888022790149    https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1     666029285002620928    https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2     666033412701032449    https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3     666044226329800704    https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4     666049248165822465    https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   
5     666050758794694657    https://pbs.twimg.com/media/CT5Jof1WUAEuVxN.jpg   
6     666051853826850816    https://pbs.twimg.com/media/CT5KoJ1WoAAJash.jpg   
7     666055525042405380    https://pbs.twimg.com/media/CT5N9tpXIAAifs1.jpg   
8     666057090499244032    https://pbs.twimg.com/media/CT5PY90WoAAQGLo.jpg   
9     666058600524156928    https://pbs.twimg.com/media/CT5Qw94XAAA_2dP.jpg   
10    666063827256086533    https://pbs.twimg.com/media/CT5Vg_wXIAAXfnj.jpg   
11    666071193221509120    https://pbs.twimg.com/media/CT5cN_3WEAAlOoZ.jpg   
12    666073100786774016    https://pbs.twimg.com/media/CT5d9DZXAAALcwe.jpg   
13    666082916733198337    https://pbs.twimg.com/media/CT5m4VGWEAAtKc8.jpg   
14    666094000022159362    https://pbs.twimg.com/media/CT5w9gUW4AAsBNN.jpg   
15    666099513787052032    https://pbs.twimg.com/media/CT51-JJUEAA6hV8.jpg   
16    666102155909144576    https://pbs.twimg.com/media/CT54YGiWUAEZnoK.jpg   
17    666104133288665088    https://pbs.twimg.com/media/CT56LSZWoAAlJj2.jpg   
18    666268910803644416    https://pbs.twimg.com/media/CT8QCd1WEAADXws.jpg   
19    666273097616637952    https://pbs.twimg.com/media/CT8T1mtUwAA3aqm.jpg   
20    666287406224695296    https://pbs.twimg.com/media/CT8g3BpUEAAuFjg.jpg   
21    666293911632134144    https://pbs.twimg.com/media/CT8mx7KW4AEQu8N.jpg   
22    666337882303524864    https://pbs.twimg.com/media/CT9OwFIWEAMuRje.jpg   
23    666345417576210432    https://pbs.twimg.com/media/CT9Vn7PWoAA_ZCM.jpg   
24    666353288456101888    https://pbs.twimg.com/media/CT9cx0tUEAAhNN_.jpg   
25    666362758909284353    https://pbs.twimg.com/media/CT9lXGsUcAAyUFt.jpg   
26    666373753744588802    https://pbs.twimg.com/media/CT9vZEYWUAAlZ05.jpg   
27    666396247373291520    https://pbs.twimg.com/media/CT-D2ZHWIAA3gK1.jpg   
28    666407126856765440    https://pbs.twimg.com/media/CT-NvwmW4AAugGZ.jpg   
29    666411507551481857    https://pbs.twimg.com/media/CT-RugiWIAELEaq.jpg   
30    666418789513326592    https://pbs.twimg.com/media/CT-YWb7U8AA7QnN.jpg   
31    666421158376562688    https://pbs.twimg.com/media/CT-aggCXAAIMfT3.jpg   
32    666428276349472768    https://pbs.twimg.com/media/CT-g-0DUwAEQdSn.jpg   
33    666430724426358785    https://pbs.twimg.com/media/CT-jNYqW4AAPi2M.jpg   
34    666435652385423360    https://pbs.twimg.com/media/CT-nsTQWEAEkyDn.jpg   
35    666437273139982337    https://pbs.twimg.com/media/CT-pKmRWIAAxUWj.jpg   
36    666447344410484738    https://pbs.twimg.com/media/CT-yU5QWwAEjLX5.jpg   
37    666454714377183233    https://pbs.twimg.com/media/CT-5Bs-WUAA2JeC.jpg   
38    666644823164719104    https://pbs.twimg.com/media/CUBl6IwVAAA9_zT.jpg   
39    666649482315059201    https://pbs.twimg.com/media/CUBqKnLWwAA5OQB.jpg   
40    666691418707132416    https://pbs.twimg.com/media/CUCQTpEWEAA7EDz.jpg   
41    666701168228331520    https://pbs.twimg.com/media/CUCZLHlUAAAeAig.jpg   
42    666739327293083650    https://pbs.twimg.com/media/CUC74aTWoAInZey.jpg   
43    666776908487630848    https://pbs.twimg.com/media/CUDeDoWUYAAD-EM.jpg   
44    666781792255496192    https://pbs.twimg.com/media/CUDigRXXIAATI_H.jpg   
45    666786068205871104    https://pbs.twimg.com/media/CUDmZIkWcAAIPPe.jpg   
46    666804364988780544    https://pbs.twimg.com/media/CUD3A7YWoAA82N0.jpg   
47    666817836334096384    https://pbs.twimg.com/media/CUEDSMEWEAAuXVZ.jpg   
48    666826780179869698    https://pbs.twimg.com/media/CUELa0NUkAAscGC.jpg   
49    666835007768551424    https://pbs.twimg.com/media/CUES51dXIA

In [17]:
archive_df

tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
0     892420643555336193                    NaN                  NaN   
1     892177421306343426                    NaN                  NaN   
2     891815181378084864                    NaN                  NaN   
3     891689557279858688                    NaN                  NaN   
4     891327558926688256                    NaN                  NaN   
5     891087950875897856                    NaN                  NaN   
6     890971913173991426                    NaN                  NaN   
7     890729181411237888                    NaN                  NaN   
8     890609185150312448                    NaN                  NaN   
9     890240255349198849                    NaN                  NaN   
10    890006608113172480                    NaN                  NaN   
11    889880896479866881                    NaN                  NaN   
12    889665388333682689                    NaN                  NaN   
13    889638837579907072                    NaN                  NaN   
14    889531135344209921                    NaN                  NaN   
15    889278841981685760                    NaN                  NaN   
16    888917238123831296                    NaN                  NaN   
17    888804989199671297                    NaN                  NaN   
18    888554962724278272                    NaN                  NaN   
19    888202515573088257                    NaN                  NaN   
20    888078434458587136                    NaN                  NaN   
21    887705289381826560                    NaN                  NaN   
22    887517139158093824                    NaN                  NaN   
23    887473957103951883                    NaN                  NaN   
24    887343217045368832                    NaN                  NaN   
25    887101392804085760                    NaN                  NaN   
26    886983233522544640                    NaN                  NaN   
27    886736880519319552                    NaN                  NaN   
28    886680336477933568                    NaN                  NaN   
29    886366144734445568                    NaN                  NaN   
30    886267009285017600           8.862664e+17         2.281182e+09   
31    886258384151887873                    NaN                  NaN   
32    886054160059072513                    NaN                  NaN   
33    885984800019947520                    NaN                  NaN   
34    885528943205470208                    NaN                  NaN   
35    885518971528720385                    NaN                  NaN   
36    885311592912609280                    NaN                  NaN   
37    885167619883638784                    NaN                  NaN   
38    884925521741709313                    NaN                  NaN   
39    884876753390489601                    NaN                  NaN   
40    884562892145688576                    NaN                  NaN   
41    884441805382717440                    NaN                  NaN   
42    884247878851493888                    NaN                  NaN   
43    884162670584377345                    NaN                  NaN   
44    883838122936631299                    NaN                  NaN   
45    883482846933004288                    NaN                  NaN   
46    883360690899218434                    NaN                  NaN   
47    883117836046086144                    NaN                  NaN   
48    882992080364220416                    NaN                  NaN   
49    882762694511734784                    NaN                  NaN   
50    882627270321602560                    NaN                  NaN   
51    882268110199369728                    NaN                  NaN   
52    882045870035918850                    NaN                  NaN   
53    881906580714921986                    NaN                  NaN   
54    881666595344535552                    NaN         

In [18]:
archive_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2356 entries, 0 to 2355
Data columns (total 17 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   tweet_id                    2356 non-null   int64  
 1   in_reply_to_status_id       78 non-null     float64
 2   in_reply_to_user_id         78 non-null     float64
 3   timestamp                   2356 non-null   object 
 4   source                      2356 non-null   object 
 5   text                        2356 non-null   object 
 6   retweeted_status_id         181 non-null    float64
 7   retweeted_status_user_id    181 non-null    float64
 8   retweeted_status_timestamp  181 non-null    object 
 9   expanded_urls               2297 non-null   object 
 10  rating_numerator            2356 non-null   int64  
 11  rating_denominator          2356 non-null   int64  
 12  name                        2356 non-null   object 
 13  doggo                       2356 

In [19]:
archive_df[['rating_numerator', 'rating_denominator']].describe().T

count       mean        std  min   25%   50%   75%  \
rating_numerator    2356.0  13.126486  45.876648  0.0  10.0  11.0  12.0   
rating_denominator  2356.0  10.455433   6.745237  0.0  10.0  10.0  10.0   

                       max  
rating_numerator    1776.0  
rating_denominator   170.0

In [20]:
archive_df['name'].value_counts()

None              745
a                  55
Charlie            12
Cooper             11
Lucy               11
Oliver             11
Penny              10
Tucker             10
Lola               10
Bo                  9
Winston             9
Sadie               8
the                 8
Buddy               7
Daisy               7
Toby                7
an                  7
Bailey              7
Bella               6
Rusty               6
Dave                6
Koda                6
Jax                 6
Milo                6
Oscar               6
Jack                6
Leo                 6
Scout               6
Stanley             6
Phil                5
Oakley              5
Chester             5
very                5
Larry               5
Alfie               5
Louis               5
Sammy               5
Bentley             5
Gus                 5
Sunny               5
Finn                5
George              5
Luna                4
Clark               4
Beau                4
Maggie    

In [21]:
archive_df.isna().sum()

tweet_id                         0
in_reply_to_status_id         2278
in_reply_to_user_id           2278
timestamp                        0
source                           0
text                             0
retweeted_status_id           2175
retweeted_status_user_id      2175
retweeted_status_timestamp    2175
expanded_urls                   59
rating_numerator                 0
rating_denominator               0
name                             0
doggo                            0
floofer                          0
pupper                           0
puppo                            0
dtype: int64

In [22]:
archive_df['doggo'].value_counts()

None     2259
doggo      97
Name: doggo, dtype: int64

In [23]:
archive_df['floofer'].value_counts()

None       2346
floofer      10
Name: floofer, dtype: int64

## Image data

In [24]:
image

tweet_id                                            jpg_url  \
0     666020888022790149    https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1     666029285002620928    https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2     666033412701032449    https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3     666044226329800704    https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4     666049248165822465    https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   
5     666050758794694657    https://pbs.twimg.com/media/CT5Jof1WUAEuVxN.jpg   
6     666051853826850816    https://pbs.twimg.com/media/CT5KoJ1WoAAJash.jpg   
7     666055525042405380    https://pbs.twimg.com/media/CT5N9tpXIAAifs1.jpg   
8     666057090499244032    https://pbs.twimg.com/media/CT5PY90WoAAQGLo.jpg   
9     666058600524156928    https://pbs.twimg.com/media/CT5Qw94XAAA_2dP.jpg   
10    666063827256086533    https://pbs.twimg.com/media/CT5Vg_wXIAAXfnj.jpg   
11    666071193221509120    https://pbs.twimg.com/media/CT5cN_3WEAAlOoZ.jpg   
12    666073100786774016    https://pbs.twimg.com/media/CT5d9DZXAAALcwe.jpg   
13    666082916733198337    https://pbs.twimg.com/media/CT5m4VGWEAAtKc8.jpg   
14    666094000022159362    https://pbs.twimg.com/media/CT5w9gUW4AAsBNN.jpg   
15    666099513787052032    https://pbs.twimg.com/media/CT51-JJUEAA6hV8.jpg   
16    666102155909144576    https://pbs.twimg.com/media/CT54YGiWUAEZnoK.jpg   
17    666104133288665088    https://pbs.twimg.com/media/CT56LSZWoAAlJj2.jpg   
18    666268910803644416    https://pbs.twimg.com/media/CT8QCd1WEAADXws.jpg   
19    666273097616637952    https://pbs.twimg.com/media/CT8T1mtUwAA3aqm.jpg   
20    666287406224695296    https://pbs.twimg.com/media/CT8g3BpUEAAuFjg.jpg   
21    666293911632134144    https://pbs.twimg.com/media/CT8mx7KW4AEQu8N.jpg   
22    666337882303524864    https://pbs.twimg.com/media/CT9OwFIWEAMuRje.jpg   
23    666345417576210432    https://pbs.twimg.com/media/CT9Vn7PWoAA_ZCM.jpg   
24    666353288456101888    https://pbs.twimg.com/media/CT9cx0tUEAAhNN_.jpg   
25    666362758909284353    https://pbs.twimg.com/media/CT9lXGsUcAAyUFt.jpg   
26    666373753744588802    https://pbs.twimg.com/media/CT9vZEYWUAAlZ05.jpg   
27    666396247373291520    https://pbs.twimg.com/media/CT-D2ZHWIAA3gK1.jpg   
28    666407126856765440    https://pbs.twimg.com/media/CT-NvwmW4AAugGZ.jpg   
29    666411507551481857    https://pbs.twimg.com/media/CT-RugiWIAELEaq.jpg   
30    666418789513326592    https://pbs.twimg.com/media/CT-YWb7U8AA7QnN.jpg   
31    666421158376562688    https://pbs.twimg.com/media/CT-aggCXAAIMfT3.jpg   
32    666428276349472768    https://pbs.twimg.com/media/CT-g-0DUwAEQdSn.jpg   
33    666430724426358785    https://pbs.twimg.com/media/CT-jNYqW4AAPi2M.jpg   
34    666435652385423360    https://pbs.twimg.com/media/CT-nsTQWEAEkyDn.jpg   
35    666437273139982337    https://pbs.twimg.com/media/CT-pKmRWIAAxUWj.jpg   
36    666447344410484738    https://pbs.twimg.com/media/CT-yU5QWwAEjLX5.jpg   
37    666454714377183233    https://pbs.twimg.com/media/CT-5Bs-WUAA2JeC.jpg   
38    666644823164719104    https://pbs.twimg.com/media/CUBl6IwVAAA9_zT.jpg   
39    666649482315059201    https://pbs.twimg.com/media/CUBqKnLWwAA5OQB.jpg   
40    666691418707132416    https://pbs.twimg.com/media/CUCQTpEWEAA7EDz.jpg   
41    666701168228331520    https://pbs.twimg.com/media/CUCZLHlUAAAeAig.jpg   
42    666739327293083650    https://pbs.twimg.com/media/CUC74aTWoAInZey.jpg   
43    666776908487630848    https://pbs.twimg.com/media/CUDeDoWUYAAD-EM.jpg   
44    666781792255496192    https://pbs.twimg.com/media/CUDigRXXIAATI_H.jpg   
45    666786068205871104    https://pbs.twimg.com/media/CUDmZIkWcAAIPPe.jpg   
46    666804364988780544    https://pbs.twimg.com/media/CUD3A7YWoAA82N0.jpg   
47    666817836334096384    https://pbs.twimg.com/media/CUEDSMEWEAAuXVZ.jpg   
48    666826780179869698    https://pbs.twimg.com/media/CUELa0NUkAAscGC.jpg   
49    666835007768551424    https://pbs.twimg.com/media/CUES51dXIA

## Image data
### Visually
> non matching names, 'shopping_cart' !=  'shopping_basket'
> 

In [25]:
image.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2075 entries, 0 to 2074
Data columns (total 12 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   tweet_id  2075 non-null   int64  
 1   jpg_url   2075 non-null   object 
 2   img_num   2075 non-null   int64  
 3   p1        2075 non-null   object 
 4   p1_conf   2075 non-null   float64
 5   p1_dog    2075 non-null   bool   
 6   p2        2075 non-null   object 
 7   p2_conf   2075 non-null   float64
 8   p2_dog    2075 non-null   bool   
 9   p3        2075 non-null   object 
 10  p3_conf   2075 non-null   float64
 11  p3_dog    2075 non-null   bool   
dtypes: bool(3), float64(3), int64(2), object(4)
memory usage: 152.1+ KB


In [26]:
image.describe()

tweet_id      img_num      p1_conf       p2_conf       p3_conf
count  2.075000e+03  2075.000000  2075.000000  2.075000e+03  2.075000e+03
mean   7.384514e+17     1.203855     0.594548  1.345886e-01  6.032417e-02
std    6.785203e+16     0.561875     0.271174  1.006657e-01  5.090593e-02
min    6.660209e+17     1.000000     0.044333  1.011300e-08  1.740170e-10
25%    6.764835e+17     1.000000     0.364412  5.388625e-02  1.622240e-02
50%    7.119988e+17     1.000000     0.588230  1.181810e-01  4.944380e-02
75%    7.932034e+17     1.000000     0.843855  1.955655e-01  9.180755e-02
max    8.924206e+17     4.000000     1.000000  4.880140e-01  2.734190e-01

**p2_conf distribution seem to have an issue**

In [27]:
sum(image.duplicated())

0

## api_df

In [28]:
api_df

tweet_id  retweet_count  favorite_count
0     892420643555336193           7001           33801
1     892177421306343426           5299           29301
2     891815181378084864           3477           22042
3     891689557279858688           7223           36920
4     891327558926688256           7754           35299
5     891087950875897856           2599           17803
6     890971913173991426           1660           10360
7     890729181411237888          15748           56838
8     890609185150312448           3617           24515
9     890240255349198849           6094           27949
10    890006608113172480           6148           27027
11    889880896479866881           4163           24554
12    889665388333682689           8343           42029
13    889638837579907072           3710           23661
14    889531135344209921           1878           13350
15    889278841981685760           4440           22107
16    888917238123831296           3759           25624
17    888804989199671297           3533           22460
18    888554962724278272           2876           17309
19    888078434458587136           2892           19146
20    887705289381826560           4532           26607
21    887517139158093824           9843           40711
22    887473957103951883          15012           60169
23    887343217045368832           8811           29582
24    887101392804085760           4986           26970
25    886983233522544640           6308           30368
26    886736880519319552           2628           10496
27    886680336477933568           3734           19726
28    886366144734445568           2629           18539
29    886267009285017600              4             105
30    886258384151887873           5283           24516
31    886054160059072513             93               0
32    885984800019947520           5607           28598
33    885528943205470208           5323           31582
34    885518971528720385           3106           17998
35    885311592912609280          15424               0
36    885167619883638784           3667           19246
37    884925521741709313          15013           67263
38    884876753390489601           4671           24374
39    884562892145688576           3907           21312
40    884441805382717440           4787           23857
41    884247878851493888          16909           63283
42    884162670584377345           2502           17938
43    883838122936631299           2860           19168
44    883482846933004288           8266           40191
45    883360690899218434           3075           19940
46    883117836046086144           5531           32511
47    882992080364220416           3243           20974
48    882762694511734784           4091           24779
49    882627270321602560           5062           24594
50    882268110199369728           9624           39186
51    882045870035918850           4080           25715
52    881906580714921986           2852           21436
53    881666595344535552           8953           44534
54    881633300179243008              8             113
55    881536004380872706          13393           43430
56    881268444196462592           4491           20473
57    880935762899988482           2332           15051
58    880872448815771648           3200           18710
59    880465832366813184           5211           25025
60    880221127280381952           3463           23661
61    880095782870896641           3650           24328
62    879862464715927552           2926           19694
63    879674319642796034              9             282
64    879492040517615616           2628           20701
65    879415818425184262          37428           92816
66    879376492567855104           2646           14854
67    879130579576475649           5739               0
68    879050749262655488           3953           19802
69    879008229531029506           2240           16779
70    878776093423087618           3432 

In [97]:
api_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2327 entries, 0 to 2326
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   tweet_id        2327 non-null   object
 1   retweet_count   2327 non-null   int64 
 2   favorite_count  2327 non-null   int64 
dtypes: int64(2), object(1)
memory usage: 54.7+ KB


## Assessing

## Quality:
### archive_df
> name column have 'a' only as a name and also have "None as a name.<br>
> Timestamp data type is not correct<br>
> several columns have missing data<br>
> Max values for rating_denominator and numerator seems extreme,<br>
> None values should be converted to NaN values<br>
> Remove html tags from source<br>
> Missing data images<br>
> arrchive dataset has retweeted data<br>
> many Id's columns 

## Tidyness(visually)
 > Dogtionary (explains the various stages of dog) is an observetion and it should be a row.<br>
 > archive data and tweets api data shold be one table, both are(e.g each observation unit forms a table)<br>
 > Image data should only have one column of the True predicted dogs and on column highest-confidence of a true prediction<br>

In [30]:
#makes dataset copies
archive_clean = archive_df.copy()
image_clean = image.copy()
api_df_clean = api_df.copy()

## Define
## TImestamp column should be in datetime data type it's in 'object' datatype

### code

In [31]:
archive_clean['timestamp'] = archive_clean['timestamp'].astype('datetime64[ns]')

### test

In [32]:
archive_clean['timestamp'].dtype

dtype('<M8[ns]')

In [33]:
archive_clean.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2356 entries, 0 to 2355
Data columns (total 17 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   tweet_id                    2356 non-null   int64         
 1   in_reply_to_status_id       78 non-null     float64       
 2   in_reply_to_user_id         78 non-null     float64       
 3   timestamp                   2356 non-null   datetime64[ns]
 4   source                      2356 non-null   object        
 5   text                        2356 non-null   object        
 6   retweeted_status_id         181 non-null    float64       
 7   retweeted_status_user_id    181 non-null    float64       
 8   retweeted_status_timestamp  181 non-null    object        
 9   expanded_urls               2297 non-null   object        
 10  rating_numerator            2356 non-null   int64         
 11  rating_denominator          2356 non-null   int64       

## Define
### None values should be converted to NaN values

In [34]:
none_columns = ['name', 'doggo', 'floofer', 'pupper', 'puppo']

for i in none_columns:
    archive_clean[i] = archive_clean[i].replace('None', np.nan)

In [35]:
archive_clean['puppo'].value_counts(dropna=False)

NaN      2326
puppo      30
Name: puppo, dtype: int64

In [36]:
archive_clean['floofer'].value_counts(dropna=False)

NaN        2346
floofer      10
Name: floofer, dtype: int64

### Define
### Remove html tags from source

In [37]:
archive_clean['source'][1]

'<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>'

### code

In [38]:
import re

def cleanhtml(raw_html):
    cleanr = re.compile('<.*?>')
    cleantext = re.sub(cleanr, '', raw_html)
    return cleantext

In [39]:
archive_clean['source']  = archive_clean['source'].apply(cleanhtml)

### Test

In [40]:
archive_clean['source'][1]

'Twitter for iPhone'

In [41]:
archive_clean['source'].value_counts()

Twitter for iPhone     2221
Vine - Make a Scene      91
Twitter Web Client       33
TweetDeck                11
Name: source, dtype: int64

## Define
### There is retweeted data in the archive dataset.(remove)

### code

In [42]:
archive_clean = archive_clean[archive_clean['retweeted_status_id'].isna()]

### test

In [43]:
archive_clean.shape

(2175, 17)

In [44]:
archive_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2175 entries, 0 to 2355
Data columns (total 17 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   tweet_id                    2175 non-null   int64         
 1   in_reply_to_status_id       78 non-null     float64       
 2   in_reply_to_user_id         78 non-null     float64       
 3   timestamp                   2175 non-null   datetime64[ns]
 4   source                      2175 non-null   object        
 5   text                        2175 non-null   object        
 6   retweeted_status_id         0 non-null      float64       
 7   retweeted_status_user_id    0 non-null      float64       
 8   retweeted_status_timestamp  0 non-null      object        
 9   expanded_urls               2117 non-null   object        
 10  rating_numerator            2175 non-null   int64         
 11  rating_denominator          2175 non-null   int64       

### Define
### Drop tweets with missing images(expanded_urls shows tweets images)

In [45]:
archive_clean['expanded_urls'].isna().sum()

58

### code

In [46]:
archive_clean = archive_clean[~archive_clean['expanded_urls'].isna()]

### test

In [47]:
archive_clean['expanded_urls'].isna().sum()

0

In [48]:
archive_clean.shape

(2117, 17)

## Define
### Some dogs name are invalid

In [49]:
archive_clean.name.value_counts(dropna=False)

NaN               622
a                  55
Charlie            11
Lucy               11
Oliver             10
Cooper             10
Tucker              9
Penny               9
Lola                8
Winston             8
Sadie               8
the                 8
Toby                7
Daisy               7
Bo                  6
Stanley             6
Oscar               6
Koda                6
Bailey              6
an                  6
Jax                 6
Bella               6
Bentley             5
Milo                5
Rusty               5
Buddy               5
Scout               5
Chester             5
Leo                 5
Louis               5
Dave                5
Larry               4
Archie              4
Jerry               4
Jack                4
Alfie               4
Dexter              4
Boomer              4
one                 4
Phil                4
Scooter             4
Gary                4
Bear                4
Finn                4
Chip                4
Reggie    

In [50]:
archive_clean.name[archive_clean.name.str.islower().fillna(False)]

22              such
56                 a
169            quite
193            quite
335              not
369              one
542       incredibly
649                a
801                a
819             very
852               my
924              one
988              not
992              his
993              one
1002               a
1004               a
1017               a
1025              an
1031            very
1040        actually
1049               a
1063            just
1071         getting
1095             mad
1097            very
1120            this
1121    unacceptable
1138             all
1193               a
1206             old
1207               a
1259     infuriating
1340               a
1351               a
1361               a
1362              an
1368               a
1382               a
1385            very
1435         getting
1457            just
1499               a
1527             the
1603             the
1693        actually
1724              by
1737         

**Lower names seems to be the ones incorrect, will replace with none values**

In [51]:
archive_clean.name[archive_clean.name.str.islower().fillna(False)] = np.nan

### test

In [52]:
archive_clean.name.value_counts(dropna=False)

NaN               726
Lucy               11
Charlie            11
Oliver             10
Cooper             10
Penny               9
Tucker              9
Lola                8
Winston             8
Sadie               8
Toby                7
Daisy               7
Bella               6
Jax                 6
Oscar               6
Stanley             6
Koda                6
Bo                  6
Bailey              6
Louis               5
Chester             5
Rusty               5
Dave                5
Buddy               5
Bentley             5
Leo                 5
Scout               5
Milo                5
Sophie              4
Archie              4
Larry               4
Alfie               4
Jack                4
Dexter              4
Scooter             4
Gary                4
Phil                4
Bear                4
Finn                4
Chip                4
Maggie              4
Duke                4
Clark               4
Cassie              4
Clarence            4
Jerry     

In [53]:
archive_clean.name[archive_clean.name.str.islower().fillna(False)]

Series([], Name: name, dtype: object)

## Define
> Several_ids columns need to be dropped and also retweed columns details.<br>
> retweeted information also should be removed.

### code

In [54]:
archive_clean.columns

Index(['tweet_id', 'in_reply_to_status_id', 'in_reply_to_user_id', 'timestamp',
       'source', 'text', 'retweeted_status_id', 'retweeted_status_user_id',
       'retweeted_status_timestamp', 'expanded_urls', 'rating_numerator',
       'rating_denominator', 'name', 'doggo', 'floofer', 'pupper', 'puppo'],
      dtype='object')

In [55]:
archive_clean.drop(['in_reply_to_status_id', 'in_reply_to_user_id', 'retweeted_status_id', 'retweeted_status_user_id', 'retweeted_status_timestamp'],\
                   axis=1, inplace=True)

### test

In [56]:
archive_clean.columns

Index(['tweet_id', 'timestamp', 'source', 'text', 'expanded_urls',
       'rating_numerator', 'rating_denominator', 'name', 'doggo', 'floofer',
       'pupper', 'puppo'],
      dtype='object')

In [57]:
archive_clean.shape

(2117, 12)

## Define
> wrong numerator and denominator ratings.(get correct values from tweets)

In [58]:
archive_clean['rating_numerator'].min()

0

## code

In [59]:
x = archive_clean['text'][516]
x

'Meet Sam. She smiles 24/7 &amp; secretly aspires to be a reindeer. \nKeep Sam smiling by clicking and sharing this link:\nhttps://t.co/98tB8y7y7t https://t.co/LouL5vdvxx'

In [60]:
import re
temp = re.findall(r'\d+/\d+', x)
temp

['24/7']

In [61]:
# regex = re.compile(r'\d+/\d')
# #archive_clean['text_ratings'] = archive_clean['text'].apply(
#                 lambda x : regex.findall(x))

In [62]:
archive_clean['text_ratings'] = archive_clean['text'].str.extract(r'(\d+/\d+)')
archive_clean['text_ratings'].sample(20)

1907    10/10
1139    11/10
1051    11/10
1275    13/10
809     12/10
947     11/10
1472    10/10
1353    10/10
2085    10/10
572     10/10
816     10/10
1344    12/10
1452    13/10
1454    12/10
1107    11/10
1450    11/10
2257    11/10
339     14/10
1965     7/10
1842    11/10
Name: text_ratings, dtype: object

In [63]:
archive_clean['text_ratings'].str.split('/', expand=True)

0    1
0       13   10
1       13   10
2       12   10
3       13   10
4       12   10
5       13   10
6       13   10
7       13   10
8       13   10
9       14   10
10      13   10
11      13   10
12      13   10
13      12   10
14      13   10
15      13   10
16      12   10
17      13   10
18      13   10
20      12   10
21      13   10
22      14   10
23      13   10
24      13   10
25      12   10
26      13   10
27      13   10
28      13   10
29      12   10
31      13   10
33      12   10
34      13   10
35      14   10
37      13   10
38      12   10
39      13   10
40      13   10
41      14   10
42      13   10
43      12   10
44      12   10
45       5   10
46      13   10
47      13   10
48      13   10
49      12   10
50      13   10
51      13   10
52      13   10
53      12   10
54      13   10
56      14   10
57      12   10
58      13   10
59      12   10
60      12   10
61      12   10
62      11   10
63      13   10
65      12   10
66      13   10
67      12   10
69      11   10
70      13   10
71      13   10
72      13   10
75      13   10
76      14   10
77      13   10
79      12   10
80      13   10
81      12   10
82      12   10
83      14   10
84      13   10
85      13   10
86      13   10
87      13   10
88      13   10
89      12   10
90      12   10
92      13   10
93      12   10
94      13   10
96      13   10
98      12   10
99      12   10
100     13   10
102     13   10
103     12   10
104     13   10
105     12   10
106     13   10
107     12   10
108     12   10
110     14   10
111     13   10
112     11   10
114     13   10
115     13   10
116     13   10
117     14   10
119     13   10
120     13   10
121     12   10
122     13   10
123     14   10
125     13   10
126     12   10
127     12   10
128     13   10
129     12   10
131     13   10
133     13   10
134     12   10
135     13   10
136     12   10
138     13   10
139     13   10
140     13   10
141     14   10
142     12   10
143     13   10
144     13   10
145     13   10
147     12   10
149     14   10
150     13   10
151     13   10
152     11   10
153     13   10
154     13   10
156     13   10
157     13   10
158     12   10
161     13   10
162     13   10
163     12   10
164     14   10
166     12   10
167     13   10
168     13   10
169     12   10
170     13   10
172     13   10
173     13   10
174     12   10
175     12   10
176     13   10
177     13   10
178     13   10
181     12   10
183     12   10
184     14   10
187     14   10
190     13   10
191     13   10
192     13   10
193     12   10
196     12   10
197     13   10
198     13   10
199     14   10
200     11   10
201     12   10
202     13   10
203     13   10
205     12   10
206     12   10
207     13   10
208     13   10
209     14   10
210     12   10
213     11   10
214     14   10
215     13   10
216     11   10
217     13   10
219     11   10
220     12   10
221     12   10
223     12   10
224     11   10
225     13   10
226     12   10
227     12   10
229      6   10
232     10   10
233     12   10
235     12   10
236     12   10
237     11   10
238     11   10
239     13   10
240     13   10
241     11   10
242     13   10
243     13   10
244     12   10
245     13   10
246     12   10
248     13   10
249     12   10
251     13   10
252     12   10
253     13   10
254     11   10
255     12   10
256     13   10
257     12   10
258     11   10
259     13   10
261     13   10
262     12   10
263     13   10
264     12   10
265     12   10
267     12   10
268     14   10
269     12   10
270     13   10
271     12   10
275     10   10
276     12   10
277     13   10
278     12   10
279     13   10
280     12   10
282     13   10
283     13   10
284     13   10
287     13   10
288     13   10
292     13   10
293     12   10
294     13   10
295     12   10
296     13   10
297     13   10
299     12   10
300     12   10
301     11   10
304     12   10
305     13   10
306     13   10
308     11   10
311     12   10
312     12   10
314     12   10
315      

In [64]:
archive_clean[['rating_numerator', 'rating_denominator']] = archive_clean['text_ratings'].str.split('/', expand=True)

In [65]:
archive_clean[['rating_numerator', 'rating_denominator']] = archive_clean[['rating_numerator', 'rating_denominator']].astype(int)

In [66]:
archive_clean.drop('text_ratings', axis=1, inplace=True)

### test

In [67]:
archive_clean[['rating_numerator', 'rating_denominator']].describe()

rating_numerator  rating_denominator
count       2117.000000         2117.000000
mean          12.246103           10.501181
std           40.275298            7.105845
min            0.000000            2.000000
25%           10.000000           10.000000
50%           11.000000           10.000000
75%           12.000000           10.000000
max         1776.000000          170.000000

In [68]:
archive_clean['rating_numerator'].idxmax()

979

In [69]:
archive_clean['text'][979]

"This is Atticus. He's quite simply America af. 1776/10 https://t.co/GRXwMxLBkh"

In [70]:
archive_clean['rating_denominator'].idxmax()

1120

In [71]:
archive_clean['text'][1120]

'Say hello to this unbelievably well behaved squad of doggos. 204/170 would try to pet all at once https://t.co/yGQI3He3xv'

## Tidiness

## Define
> Dog stages is an observation should be put into a column

In [72]:
archive_clean.columns

Index(['tweet_id', 'timestamp', 'source', 'text', 'expanded_urls',
       'rating_numerator', 'rating_denominator', 'name', 'doggo', 'floofer',
       'pupper', 'puppo'],
      dtype='object')

### code

In [73]:
archive_clean['dog_stage'] = archive_clean[['doggo', 'floofer', 'pupper', 'puppo']].replace(np.nan, '').sum(1)

In [74]:
archive_clean['dog_stage'] = archive_clean['dog_stage'].replace('', np.nan)

In [75]:
archive_clean.drop(['doggo', 'floofer', 'pupper', 'puppo'], axis=1, inplace=True)

### test

In [76]:
archive_clean['dog_stage'].value_counts(dropna=False)

NaN             1779
pupper           222
doggo             72
puppo             23
doggopupper       10
floofer            9
doggofloofer       1
doggopuppo         1
Name: dog_stage, dtype: int64

In [77]:
archive_clean.head()

tweet_id           timestamp              source  \
0  892420643555336193 2017-08-01 16:23:56  Twitter for iPhone   
1  892177421306343426 2017-08-01 00:17:27  Twitter for iPhone   
2  891815181378084864 2017-07-31 00:18:03  Twitter for iPhone   
3  891689557279858688 2017-07-30 15:58:51  Twitter for iPhone   
4  891327558926688256 2017-07-29 16:00:24  Twitter for iPhone   

                                                text  \
0  This is Phineas. He's a mystical boy. Only eve...   
1  This is Tilly. She's just checking pup on you....   
2  This is Archie. He is a rare Norwegian Pouncin...   
3  This is Darla. She commenced a snooze mid meal...   
4  This is Franklin. He would like you to stop ca...   

                                       expanded_urls  rating_numerator  \
0  https://twitter.com/dog_rates/status/892420643...                13   
1  https://twitter.com/dog_rates/status/892177421...                13   
2  https://twitter.com/dog_rates/status/891815181...                12   
3  https://twitter.com/dog_rates/status/891689557...                13   
4  https://twitter.com/dog_rates/status/891327558...                12   

   rating_denominator      name dog_stage  
0                  10   Phineas       NaN  
1                  10     Tilly       NaN  
2                  10    Archie       NaN  
3                  10     Darla       NaN  
4                  10  Franklin       NaN

## Define
> api dataframe should be merged to archive dataframe to have 1 dataframe(each type of observation forms a table)

### code

In [78]:
api_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2327 entries, 0 to 2326
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   tweet_id        2327 non-null   object
 1   retweet_count   2327 non-null   int64 
 2   favorite_count  2327 non-null   int64 
dtypes: int64(2), object(1)
memory usage: 54.7+ KB


**to merge convert archive_clean tweet_id to object data type)**

In [79]:
archive_clean['tweet_id'] = archive_clean['tweet_id'].apply(str)

In [80]:
df = archive_clean.merge(api_df, how='inner', on='tweet_id')

### test

In [81]:
df.head()

tweet_id           timestamp              source  \
0  892420643555336193 2017-08-01 16:23:56  Twitter for iPhone   
1  892177421306343426 2017-08-01 00:17:27  Twitter for iPhone   
2  891815181378084864 2017-07-31 00:18:03  Twitter for iPhone   
3  891689557279858688 2017-07-30 15:58:51  Twitter for iPhone   
4  891327558926688256 2017-07-29 16:00:24  Twitter for iPhone   

                                                text  \
0  This is Phineas. He's a mystical boy. Only eve...   
1  This is Tilly. She's just checking pup on you....   
2  This is Archie. He is a rare Norwegian Pouncin...   
3  This is Darla. She commenced a snooze mid meal...   
4  This is Franklin. He would like you to stop ca...   

                                       expanded_urls  rating_numerator  \
0  https://twitter.com/dog_rates/status/892420643...                13   
1  https://twitter.com/dog_rates/status/892177421...                13   
2  https://twitter.com/dog_rates/status/891815181...                12   
3  https://twitter.com/dog_rates/status/891689557...                13   
4  https://twitter.com/dog_rates/status/891327558...                12   

   rating_denominator      name dog_stage  retweet_count  favorite_count  
0                  10   Phineas       NaN           7001           33801  
1                  10     Tilly       NaN           5299           29301  
2                  10    Archie       NaN           3477           22042  
3                  10     Darla       NaN           7223           36920  
4                  10  Franklin       NaN           7754           35299

In [82]:
df.shape

(2109, 11)

## Define
> only take the true predicted image, with high confidence

In [83]:
image.head()

tweet_id                                          jpg_url  \
0  666020888022790149  https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1  666029285002620928  https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2  666033412701032449  https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3  666044226329800704  https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4  666049248165822465  https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   

   img_num                      p1   p1_conf  p1_dog                  p2  \
0        1  Welsh_springer_spaniel  0.465074    True              collie   
1        1                 redbone  0.506826    True  miniature_pinscher   
2        1         German_shepherd  0.596461    True            malinois   
3        1     Rhodesian_ridgeback  0.408143    True             redbone   
4        1      miniature_pinscher  0.560311    True          Rottweiler   

    p2_conf  p2_dog                   p3   p3_conf  p3_dog  
0  0.156665    True    Shetland_sheepdog  0.061428    True  
1  0.074192    True  Rhodesian_ridgeback  0.072010    True  
2  0.138584    True           bloodhound  0.116197    True  
3  0.360687    True   miniature_pinscher  0.222752    True  
4  0.243682    True             Doberman  0.154629    True

In [84]:
# prediction order were in order of confidence of model prediction
for index,row in image_clean.iterrows():
    if row['p1_dog'] == True:
        image_clean.at[index,'prediction_conf'] = row['p1_conf']
        image_clean.at[index,'dog_breed_pred'] = row['p1']
        
    elif row['p2_dog'] == True:
        image_clean.at[index,'prediction_conf'] = row['p2_conf']
        image_clean.at[index,'dog_breed_pred'] = row['p2']
    
    elif row['p3_dog'] == True:
        image_clean.at[index,'prediction_conf'] = row['p3_conf']
        image_clean.at[index,'dog_breed_pred'] = row['p3']

In [85]:
image_clean = image_clean[['tweet_id', 'jpg_url','img_num', 'dog_breed_pred', 'prediction_conf']]

## Define
> merge image data into former merged dataframe

### code

In [86]:
image_clean.shape

(2075, 5)

In [87]:
image_clean['tweet_id'] = image_clean['tweet_id'].apply(str)

In [88]:
final_df = df.merge(image_clean, how='inner', on='tweet_id')

### test 

In [89]:
final_df.head()

tweet_id           timestamp              source  \
0  892420643555336193 2017-08-01 16:23:56  Twitter for iPhone   
1  892177421306343426 2017-08-01 00:17:27  Twitter for iPhone   
2  891815181378084864 2017-07-31 00:18:03  Twitter for iPhone   
3  891689557279858688 2017-07-30 15:58:51  Twitter for iPhone   
4  891327558926688256 2017-07-29 16:00:24  Twitter for iPhone   

                                                text  \
0  This is Phineas. He's a mystical boy. Only eve...   
1  This is Tilly. She's just checking pup on you....   
2  This is Archie. He is a rare Norwegian Pouncin...   
3  This is Darla. She commenced a snooze mid meal...   
4  This is Franklin. He would like you to stop ca...   

                                       expanded_urls  rating_numerator  \
0  https://twitter.com/dog_rates/status/892420643...                13   
1  https://twitter.com/dog_rates/status/892177421...                13   
2  https://twitter.com/dog_rates/status/891815181...                12   
3  https://twitter.com/dog_rates/status/891689557...                13   
4  https://twitter.com/dog_rates/status/891327558...                12   

   rating_denominator      name dog_stage  retweet_count  favorite_count  \
0                  10   Phineas       NaN           7001           33801   
1                  10     Tilly       NaN           5299           29301   
2                  10    Archie       NaN           3477           22042   
3                  10     Darla       NaN           7223           36920   
4                  10  Franklin       NaN           7754           35299   

                                           jpg_url  img_num  \
0  https://pbs.twimg.com/media/DGKD1-bXoAAIAUK.jpg        1   
1  https://pbs.twimg.com/media/DGGmoV4XsAAUL6n.jpg        1   
2  https://pbs.twimg.com/media/DGBdLU1WsAANxJ9.jpg        1   
3  https://pbs.twimg.com/media/DF_q7IAWsAEuuN8.jpg        1   
4  https://pbs.twimg.com/media/DF6hr6BUMAAzZgT.jpg        2   

       dog_breed_pred  prediction_conf  
0                 NaN              NaN  
1           Chihuahua         0.323581  
2           Chihuahua         0.716012  
3  Labrador_retriever         0.168086  
4              basset         0.555712

In [90]:
final_df.shape

(1986, 15)

## Storing clean data

In [91]:
final_df.to_csv('twitter_archive_master.csv', index=False)